# This is a sample Jupyter Notebook

Below is an example of a code cell. 
Put your cursor into the cell and press Shift+Enter to execute it and select the next one, or click 'Run Cell' button.

Press Double Shift to search everywhere for classes, files, tool windows, actions, and settings.

To learn more about Jupyter Notebooks in PyCharm, see [help](https://www.jetbrains.com/help/pycharm/ipython-notebook-support.html).
For an overview of PyCharm, go to Help -> Learn IDE features or refer to [our documentation](https://www.jetbrains.com/help/pycharm/getting-started.html).

In [3]:
# 获取ID数据

import requests

headers = {
    'accept': '*/*',
    'accept-language': 'zh-CN,zh;q=0.9',
    'content-type': 'application/json',
    'dnt': '1',
    'origin': 'https://www.mianshiya.com',
    'priority': 'u=1, i',
    'referer': 'https://www.mianshiya.com/',
    'sec-ch-ua': '"Chromium";v="142", "Google Chrome";v="142", "Not_A Brand";v="99"',
    'sec-ch-ua-mobile': '?0',
    'sec-ch-ua-platform': '"macOS"',
    'sec-fetch-dest': 'empty',
    'sec-fetch-mode': 'cors',
    'sec-fetch-site': 'same-site',
    'sec-gpc': '1',
    'user-agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/142.0.0.0 Safari/537.36',
}

json_data = {
    'current': 1,
    'pageSize': 1000,
}

response = requests.post('https://api.mianshiya.com/api/question_bank/list/page/vo', headers=headers, json=json_data)

# 确认请求成功
bank_list = []
if response.status_code == 200:
    # 解析 JSON 数据为字典
    data = response.json()

    # 假设 JSON 中有一个 "user" 字段，里面有 "id"、"name" 和 "email"
    records = data['data']['records']
    for record in records:
        id = record['id']
        title = record['title']
        # print(id)
        # print(title)
        bank_list.append({"id": id,"title": title})
else:
    print(f"请求失败，状态码：{response.status_code}")

# print(bank_list)

In [4]:
# 获取题目数据
import requests
import re
import json

headers = {
    'accept': '*/*',
    'accept-language': 'zh-CN,zh;q=0.9',
    'content-type': 'application/json',
    'dnt': '1',
    'origin': 'https://www.mianshiya.com',
    'priority': 'u=1, i',
    'referer': 'https://www.mianshiya.com/',
    'sec-ch-ua': '"Chromium";v="142", "Google Chrome";v="142", "Not_A Brand";v="99"',
    'sec-ch-ua-mobile': '?0',
    'sec-ch-ua-platform': '"macOS"',
    'sec-fetch-dest': 'empty',
    'sec-fetch-mode': 'cors',
    'sec-fetch-site': 'same-site',
    'sec-gpc': '1',
    'user-agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/142.0.0.0 Safari/537.36',
}

json_data = {
    'current': 1,
    'pageSize': 20,
    'questionBankId': '1791375592078610434',
    'tagList': [],
}

response = requests.post('https://api.mianshiya.com/api/question_bank/list_question', headers=headers, json=json_data)

# Note: json_data will not be serialized by requests
# exactly as it was in the original request.
#data = '{"questionBankId":"1791375592078610434","current":1,"pageSize":200}'
#response = requests.post('https://api.mianshiya.com/api/question_bank/list_question', headers=headers, data=data)
# start_index = 0
question_list = []
for bank in bank_list :
    # start_index = start_index + 1
    # if start_index not in [ 276]: # 16 95 113 206 274 276
    #     continue
    json_data['questionBankId'] = bank['id']
    response = requests.post('https://api.mianshiya.com/api/question_bank/list_question', headers=headers, json=json_data)
    # print(response.json())
    # 保存到文件，比如保存为 user_info.json
    # with open(bank['title'] + '.json', 'w', encoding='utf-8') as f:
    #     json.dump(response.json(), f, ensure_ascii=False, indent=4)
    size = response.json()["data"]["total"]
    # print("order: ", start_index)
    print("title: ", bank['title'])
    # print("题目数量: ", size)
    
    # 如果题目数量超过200，则分页获取
    all_records = []
    if int(size) > 200:
        # 计算需要多少页（每页100条）
        pages = (int(size) + 99) // 100  # 向上取整
        # print(f"题目数量超过200，共{size}题，需要分{pages}页获取")
        
        # 分页获取所有数据
        for page in range(1, pages + 1):
            json_data['current'] = page
            json_data['pageSize'] = 100
            response = requests.post('https://api.mianshiya.com/api/question_bank/list_question', headers=headers, json=json_data)
            if response.status_code == 200:
                records = response.json()["data"]["records"]
                all_records.extend(records)
                print(f"已获取第{page}页，共{len(records)}题")
            else:
                print(f"获取第{page}页数据失败，状态码：{response.status_code}")
    else:
        # 题目数量不超过200，一次性获取
        json_data['pageSize'] = size if int(size) > 0 else 200
        json_data['current'] = 1
        response = requests.post('https://api.mianshiya.com/api/question_bank/list_question', headers=headers, json=json_data)
        if response.status_code == 200:
            all_records = response.json()["data"]["records"]
        else:
            print(f"获取数据失败，状态码：{response.status_code}")
    
    # 所有数据获取完成后写入文件
    safe_title = re.sub(r'[\\/:*?"<>|]', '_', bank['title'])
    filename = safe_title + ".md"
    with open(filename, "w") as f:
        for record in all_records:
            title = record['title']
            f.write( title + "\n")
            f.write("---\n")
    print(f"已将{len(all_records)}题写入文件{filename}")

title:  Java 基础面试题
已将65题写入文件Java 基础面试题.md
title:  腾讯 Java 面经
已将14题写入文件腾讯 Java 面经.md
title:  小米 Java 面经
已将9题写入文件小米 Java 面经.md
title:  Java 集合面试题
已将26题写入文件Java 集合面试题.md
title:  Java 并发面试题
已将63题写入文件Java 并发面试题.md
title:  Java 虚拟机面试题
已将46题写入文件Java 虚拟机面试题.md
title:  Spring 面试题
已将71题写入文件Spring 面试题.md
title:  操作系统面试题
已将22题写入文件操作系统面试题.md
title:  计算机网络面试题
已将37题写入文件计算机网络面试题.md
title:  MySQL 面试题
已将81题写入文件MySQL 面试题.md
title:  Redis 面试题
已将53题写入文件Redis 面试题.md
title:  后端系统设计面试题
已将22题写入文件后端系统设计面试题.md
title:  后端场景面试题
已将110题写入文件后端场景面试题.md
title:  SpringBoot 面试题
已将26题写入文件SpringBoot 面试题.md
title:  SpringCloud 面试题
已将55题写入文件SpringCloud 面试题.md
title:  408考研面试题
已获取第1页，共100题
已获取第2页，共100题
已获取第3页，共100题
已获取第4页，共100题
已获取第5页，共47题
已将447题写入文件408考研面试题.md
title:  智力题
已将60题写入文件智力题.md
title:  伙伴匹配项目面试题
已将27题写入文件伙伴匹配项目面试题.md
title:  智能 BI 项目面试题
已将32题写入文件智能 BI 项目面试题.md
title:  API 开放平台项目面试题
已将28题写入文件API 开放平台项目面试题.md
title:  用户中心项目面试题
已将24题写入文件用户中心项目面试题.md
title:  后端经典面试题合集
已将82题写入文件后端经典面试题合集.md
title:  聚合搜索项目面试题
已将27题写入文件聚合